# Requirements

In [1]:
# for model, training
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable

device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f'torch verion: {torch.__version__}')

torch verion: 1.0.1.post2


In [2]:
# for data
from torchtext import data, datasets
import torchtext
import spacy

In [3]:
# for visualization
from IPython.display import Image
import matplotlib.pyplot as plt
import seaborn

seaborn.set_context(context="talk")
%matplotlib inline

In [4]:
# other utils
import math, copy, time
import numpy as np

# Model

## Skeleton

In [5]:
class EncoderDecoder(nn.Module):
    """
    A standard Encoder-Decoder architecture. Base for this and many 
    other models.
    """
    def __init__(self, encoder, decoder, src_embed, tgt_embed, generator):
        super(EncoderDecoder, self).__init__()
        self.encoder = encoder
        self.decoder = decoder
        self.src_embed = src_embed
        self.tgt_embed = tgt_embed
        self.generator = generator
        
    def forward(self, src, tgt, src_mask, tgt_mask):
        "Take in and process masked src and target sequences."
        return self.decode(self.encode(src, src_mask), src_mask,
                            tgt, tgt_mask)
    
    def encode(self, src, src_mask):
        return self.encoder(self.src_embed(src), src_mask)
    
    def decode(self, memory, src_mask, tgt, tgt_mask):
        return self.decoder(self.tgt_embed(tgt), memory, src_mask, tgt_mask)

In [6]:
class Generator(nn.Module):
    "Define standard linear + softmax generation step."
    def __init__(self, d_model, vocab):
        super(Generator, self).__init__()
        self.proj = nn.Linear(d_model, vocab)

    def forward(self, x):
        return F.log_softmax(self.proj(x), dim=-1)

In [7]:
def clones(module, N):
    "Produce N identical layers."
    return nn.ModuleList([copy.deepcopy(module) for _ in range(N)])

## Common

### Embedding

In [8]:
class Embeddings(nn.Module):
    def __init__(self, d_model, vocab):
        super(Embeddings, self).__init__()
        self.lut = nn.Embedding(vocab, d_model)
        self.d_model = d_model

    def forward(self, x):
        return self.lut(x) * math.sqrt(self.d_model)

### Positional Encoding

In [9]:
class PositionalEncoding(nn.Module):
    "Implement the PE function."
    def __init__(self, d_model, dropout, max_len=5000):
        super(PositionalEncoding, self).__init__()
        self.dropout = nn.Dropout(p=dropout)
        
        # Compute the positional encodings once in log space.
        pe = torch.zeros(max_len, d_model)
        position = torch.arange(0., max_len).unsqueeze(1)
        div_term = torch.exp(torch.arange(0., d_model, 2) * -(math.log(10000.0) / d_model))
        pe[:, 0::2] = torch.sin(position * div_term)
        pe[:, 1::2] = torch.cos(position * div_term)
        pe = pe.unsqueeze(0)
        self.register_buffer('pe', pe)
        
    def forward(self, x):
        x = x + Variable(self.pe[:, :x.size(1)], 
                         requires_grad=False)
        return self.dropout(x)

### Multi-Head attention

In [10]:
def attention(query, key, value, mask=None, dropout=None):
    "Compute 'Scaled Dot Product Attention'"
    d_k = query.size(-1)
    scores = torch.matmul(query, key.transpose(-2, -1)) \
             / math.sqrt(d_k)
    if mask is not None:
        scores = scores.masked_fill(mask == 0, -1e9)
    p_attn = F.softmax(scores, dim = -1)
    if dropout is not None:
        p_attn = dropout(p_attn)
    return torch.matmul(p_attn, value), p_attn

class MultiHeadedAttention(nn.Module):
    def __init__(self, h, d_model, dropout=0.1):
        "Take in model size and number of heads."
        super(MultiHeadedAttention, self).__init__()
        assert d_model % h == 0
        # We assume d_v always equals d_k
        self.d_k = d_model // h
        self.h = h
        self.linears = clones(nn.Linear(d_model, d_model), 4)
        self.attn = None
        self.dropout = nn.Dropout(p=dropout)
        
    def forward(self, query, key, value, mask=None):
        "Implements Figure 2"
        if mask is not None:
            # Same mask applied to all h heads.
            mask = mask.unsqueeze(1)
        nbatches = query.size(0)
        
        # 1) Do all the linear projections in batch from d_model => h x d_k 
        query, key, value = \
            [l(x).view(nbatches, -1, self.h, self.d_k).transpose(1, 2)
             for l, x in zip(self.linears, (query, key, value))]
        
        # 2) Apply attention on all the projected vectors in batch. 
        x, self.attn = attention(query, key, value, mask=mask, 
                                 dropout=self.dropout)
        
        # 3) "Concat" using a view and apply a final linear. 
        x = x.transpose(1, 2).contiguous() \
             .view(nbatches, -1, self.h * self.d_k)
        return self.linears[-1](x)

### Feed Forward

In [11]:
class PositionwiseFeedForward(nn.Module):
    "Implements FFN equation."
    def __init__(self, d_model, d_ff, dropout=0.1):
        super(PositionwiseFeedForward, self).__init__()
        self.w_1 = nn.Linear(d_model, d_ff)
        self.w_2 = nn.Linear(d_ff, d_model)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x):
        return self.w_2(self.dropout(F.relu(self.w_1(x))))

In [12]:
def subsequent_mask(size):
    "Mask out subsequent positions."
    attn_shape = (1, size, size)
    subsequent_mask = np.triu(np.ones(attn_shape), k=1).astype('uint8')
    return torch.from_numpy(subsequent_mask) == 0

## Encoder

In [13]:
class Encoder(nn.Module):
    "Core encoder is a stack of N layers"
    def __init__(self, layer, N):
        super(Encoder, self).__init__()
        self.layers = clones(layer, N)
        self.norm = LayerNorm(layer.size)
        
    def forward(self, x, mask):
        "Pass the input (and mask) through each layer in turn."
        for layer in self.layers:
            x = layer(x, mask)
        return self.norm(x)

In [14]:
class LayerNorm(nn.Module):
    "Construct a layernorm module (See citation for details)."
    def __init__(self, features, eps=1e-6):
        super(LayerNorm, self).__init__()
        self.a_2 = nn.Parameter(torch.ones(features))
        self.b_2 = nn.Parameter(torch.zeros(features))
        self.eps = eps

    def forward(self, x):
        mean = x.mean(-1, keepdim=True)
        std = x.std(-1, keepdim=True)
        return self.a_2 * (x - mean) / (std + self.eps) + self.b_2

In [15]:
class EncoderLayer(nn.Module):
    "Encoder is made up of self-attn and feed forward (defined below)"
    def __init__(self, size, self_attn, feed_forward, dropout):
        super(EncoderLayer, self).__init__()
        self.self_attn = self_attn
        self.feed_forward = feed_forward
        self.sublayer = clones(SublayerConnection(size, dropout), 2)
        self.size = size

    def forward(self, x, mask):
        "Follow Figure 1 (left) for connections."
        x = self.sublayer[0](x, lambda x: self.self_attn(x, x, x, mask))
        return self.sublayer[1](x, self.feed_forward)

In [16]:
class SublayerConnection(nn.Module):
    """
    A residual connection followed by a layer norm.
    Note for code simplicity the norm is first as opposed to last.
    """
    def __init__(self, size, dropout):
        super(SublayerConnection, self).__init__()
        self.norm = LayerNorm(size)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x, sublayer):
        "Apply residual connection to any sublayer with the same size."
        return x + self.dropout(sublayer(self.norm(x)))

## Decoder

In [17]:
class Decoder(nn.Module):
    "Generic N layer decoder with masking."
    def __init__(self, layer, N):
        super(Decoder, self).__init__()
        self.layers = clones(layer, N)
        self.norm = LayerNorm(layer.size)
        
    def forward(self, x, memory, src_mask, tgt_mask):
        for layer in self.layers:
            x = layer(x, memory, src_mask, tgt_mask)
        return self.norm(x)

In [18]:
class DecoderLayer(nn.Module):
    "Decoder is made of self-attn, src-attn, and feed forward (defined below)"
    def __init__(self, size, self_attn, src_attn, feed_forward, dropout):
        super(DecoderLayer, self).__init__()
        self.size = size
        self.self_attn = self_attn
        self.src_attn = src_attn
        self.feed_forward = feed_forward
        self.sublayer = clones(SublayerConnection(size, dropout), 3)
 
    def forward(self, x, memory, src_mask, tgt_mask):
        "Follow Figure 1 (right) for connections."
        m = memory
        x = self.sublayer[0](x, lambda x: self.self_attn(x, x, x, tgt_mask))
        x = self.sublayer[1](x, lambda x: self.src_attn(x, m, m, src_mask))
        return self.sublayer[2](x, self.feed_forward)

_________________________________
## Complete Model

In [19]:
def make_model(src_vocab, tgt_vocab, N=6, 
               d_model=512, d_ff=2048, h=8, dropout=0.1):
    "Helper: Construct a model from hyperparameters."
    c = copy.deepcopy
    attn = MultiHeadedAttention(h, d_model)
    ff = PositionwiseFeedForward(d_model, d_ff, dropout)
    position = PositionalEncoding(d_model, dropout)
    model = EncoderDecoder(
        Encoder(EncoderLayer(d_model, c(attn), c(ff), dropout), N),
        Decoder(DecoderLayer(d_model, c(attn), c(attn), 
                             c(ff), dropout), N),
        nn.Sequential(Embeddings(d_model, src_vocab), c(position)),
        nn.Sequential(Embeddings(d_model, tgt_vocab), c(position)),
        Generator(d_model, tgt_vocab))
    
    # This was important from their code. 
    # Initialize parameters with Glorot / fan_avg.
    for p in model.parameters():
        if p.dim() > 1:
            nn.init.xavier_uniform_(p)
    return model

_____________________________________________

# Data

## Loading (spacy + torchtext)

In [20]:
def load_data(src, trg):
    
    spacy_src = spacy.load(src)
    spacy_trg = spacy.load(trg)

    def tokenize_src(text):
        return [tok.text for tok in spacy_src.tokenizer(text)]

    def tokenize_trg(text):
        return [tok.text for tok in spacy_trg.tokenizer(text)]
    
    SOS_WORD, EOS_WORD, BLANK_WORD = '<s>', '</s>', '<blank>'
    SRC = data.Field(tokenize=tokenize_src, pad_token=BLANK_WORD)
    TGT = data.Field(tokenize=tokenize_trg, init_token = SOS_WORD, eos_token = EOS_WORD, pad_token=BLANK_WORD)
    
    data_fields = [('English', SRC), ('French', TGT)]
    
    train, val = data.TabularDataset.splits(path='./data/', 
                                            train='train.csv', validation='val.csv', format='csv', 
                                            fields=data_fields)
    
    SRC.build_vocab(train, val)
    TGT.build_vocab(train, val)
    
    return SRC, TGT, train, val

In [21]:
%%time
SRC, TGT, train, val = load_data(src='en', trg='fr')

CPU times: user 14 s, sys: 184 ms, total: 14.2 s
Wall time: 14.5 s


In [22]:
%%time
train_iter = data.BucketIterator(train, batch_size=20, sort_key=lambda x: len(x.French), shuffle=True)

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 37 µs


## Batches and Masking

In [45]:
def rebatch(pad_idx, batch):
    "Fix order in torchtext to match ours"
    src, trg = batch.English.transpose(0, 1), batch.French.transpose(0, 1)
    return Batch(src, trg, pad_idx)

class Batch:
    "Object for holding a batch of data with mask during training."
    def __init__(self, src, trg=None, pad=0):
        self.src = src
        self.src_mask = (src != pad).unsqueeze(-2)
        if trg is not None:
            self.trg = trg[:, :-1]
            self.trg_y = trg[:, 1:]
            self.trg_mask = self.make_std_mask(self.trg, pad)
            self.ntokens = (self.trg_y != pad).data.sum()
    
    @staticmethod
    def make_std_mask(tgt, pad):
        "Create a mask to hide padding and future words."
        tgt_mask = (tgt != pad).unsqueeze(-2)
        tgt_mask = tgt_mask & Variable(
            subsequent_mask(tgt.size(-1)).type_as(tgt_mask.data))
        return tgt_mask

# Training

## Training Loop

In [114]:
def run_epoch(data_iter, model, loss_compute, num_batches):
    total_loss = 0
    
    for idx, batch in enumerate(data_iter):
        out = model(batch.src, batch.trg, 
                    batch.src_mask, batch.trg_mask)
        loss = loss_compute(out, batch.trg_y, batch.src.shape[0])
        total_loss += loss

        if (idx + 1) % 200 == 1:
            print(f'batches elapsed: {idx + 1} loss: {loss}')
            
    return total_loss / num_batches

## Loss Computation (backprop)

In [115]:
class SimpleLossCompute:
    "A simple loss compute and train function."
    def __init__(self, generator, criterion, optimizer):
        self.generator = generator
        self.criterion = criterion
        self.optimizer = optimizer
        
    def __call__(self, x, y, norm):
        x = self.generator(x)
        loss = 0
        for idx in range(norm):
            loss += self.criterion(x[idx], y[idx])
        
        loss /= norm
        
        self.optimizer.zero_grad()
        loss.backward()
        self.optimizer.step()
        
        return loss.item()

In [116]:
model = make_model(len(SRC.vocab.itos), len(TGT.vocab.itos), N=2)
loss_criteria = SimpleLossCompute(model.generator, nn.CrossEntropyLoss(), torch.optim.Adam(model.parameters()))
pad_idx = TGT.vocab.stoi['<blank>']

In [117]:
%%time
model.train()
epochs = 7
for epoch in range(epochs):
    print(f'EPOCH {epoch}===============\n')
    epoch_loss = run_epoch((rebatch(pad_idx, b) for b in train_iter), 
                           model, loss_criteria, len(train_iter))
    
    print(f'FINAL {epoch} loss: {epoch_loss}')
    print(f'\nEPOCH {epoch}===============\n')

EPOCH 0===============

batches elapsed: 1 loss: 9.621870040893555
batches elapsed: 201 loss: 2.798128128051758
FINAL 0 loss: 2.858115151482804

EPOCH 0===============

EPOCH 1===============

batches elapsed: 1 loss: 2.8250603675842285
batches elapsed: 201 loss: 2.146256923675537
FINAL 1 loss: 2.2768258737916707

EPOCH 1===============

EPOCH 2===============

batches elapsed: 1 loss: 2.0244860649108887
batches elapsed: 201 loss: 1.6325130462646484
FINAL 2 loss: 2.0178429546142493

EPOCH 2===============

EPOCH 3===============

batches elapsed: 1 loss: 1.6413732767105103
batches elapsed: 201 loss: 1.6596319675445557
FINAL 3 loss: 1.847574729211524

EPOCH 3===============

EPOCH 4===============

batches elapsed: 1 loss: 2.0786452293395996
batches elapsed: 201 loss: 1.6277015209197998
FINAL 4 loss: 1.6835230712463207

EPOCH 4===============

EPOCH 5===============

batches elapsed: 1 loss: 1.519148588180542
batches elapsed: 201 loss: 1.7074006795883179
FINAL 5 loss: 1.575989499312489


In [118]:
torch.save({
            'transformer': model.state_dict(),
            'optimizer_state_dict': loss_criteria.optimizer.state_dict()
            }, './model.tar')
print(f'saved to ./model.tar')

saved to ./model.tar


## Translation (evaluation)

In [101]:
def greedy_decode(model, src, src_mask, max_len, start_symbol):
    memory = model.encode(src, src_mask)
    ys = torch.ones(1, 1).fill_(start_symbol).type_as(src.data)
    for i in range(max_len-1):
        out = model.decode(memory, src_mask, 
                           Variable(ys), 
                           Variable(subsequent_mask(ys.size(1))
                                    .type_as(src.data)))
        prob = model.generator(out[:, -1])
        _, next_word = torch.max(prob, dim = 1)
        next_word = next_word.data[0]
        ys = torch.cat([ys, 
                        torch.ones(1, 1).type_as(src.data).fill_(next_word)], dim=1)
    
    return ys

In [119]:
model.eval()
valid_iter = data.BucketIterator(val, batch_size=1, sort_key=lambda x: len(x.French), shuffle=True)
valid_iter = (rebatch(pad_idx, b) for b in valid_iter)

In [123]:
for i, batch in enumerate(valid_iter):
    src = batch.src.transpose(0, 1)[:1]
    src_mask = (src != SRC.vocab.stoi['<blank>']).unsqueeze(-2)
    out = greedy_decode(model, src, src_mask, 
                        max_len=60, start_symbol=TGT.vocab.stoi['<s>'])
    
    print('\nsource:\t')
    src = batch.src[0]
    for i in range(src.shape[0]):
        sym = SRC.vocab.itos[src[i]]
        if sym == "</s>": break
        print(sym, end =" ")
    
    print('\n\ntranslation:\t')
    for i in range(1, out.size(1)):
        sym = TGT.vocab.itos[out[0, i]]
        if sym == '</s>': break
        print(sym, end =' ')

    print('\n\ntarget:\t')
    target = batch.trg[0]
    for i in range(target.shape[0]):
        sym = TGT.vocab.itos[target[i]]
        if sym == '</s>': break
        print(sym, end =' ')

    break


source:	
Thank you , Commissioner , for your statement . 

translation:	
séance est clos . 

target:	
<s> Merci , Monsieur le Commissaire , pour votre déclaration . 